# Cohort Building

**Example use case:** 

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" alt="alt_text" align="left"
	width="150" height="150" />
Julia is an oncologist that specializes in female reproductive health. As part of her research, she is interested in  using existing data on uterine cancers. If possible, she would like to see multiple datatypes (gross imaging, genomic data, proteomic data, histology) that come from the same patient, so she can look for shared phenotypes to test for their potential as early diagnostics. Julia heard that the Cancer Data Aggregator has made it easy to search across multiple datasets created by NCI, and so has decided to start her search there.



## Getting Started

The CDA provides a custom python tool for searching CDA data. [`Q`](usage/#q) (short for Query) offers several ways to search and filter data, and several input modes:

---
- **<a href="../../QuickStart/usage/#q">Q.()</a>** builds a query that can be used by `run()` or `count()`
- **<a href="../../QuickStart/usage/#qrun">Q.run()</a>** returns data for the specified search 
- **<a href="../../QuickStart/usage/#qcount">Q.count()</a>** returns summary information (counts) data that fit the specified search
- **<a href="../../QuickStart/usage/#columns">columns()</a>** returns entity field names
- **<a href="../../QuickStart/usage/#unique_terms">unique_terms()</a>** returns entity field contents

---

Before Julia does any work, she needs to import these functions cdapython.
She'll also need to import [pandas](https://pandas.pydata.org/) to work with dataframes and itables to display them nicely. The `opt.` settings are pre-configuring how itables should display her tables, with scrolling and paging enabled.

In [1]:
from cdapython import Q, columns, unique_terms, query
import numpy as np
import pandas as pd
from itables import init_notebook_mode, show
init_notebook_mode(all_interactive=True)
import itables.options as opt
opt.maxBytes=0
opt.scrollX="200px"
opt.scrollCollapse=True
opt.paging=True
opt.maxColumns=0
print(Q.get_version())

<IPython.core.display.Javascript object>

2022.10.24

<div class="cdanote" style="background-color:#b3e5d5;color:black;padding:20px;">
    
    
CDA data comes from three sources:
<ul>
<li><b>The <a href="https://proteomic.datacommons.cancer.gov/pdc/"> Proteomic Data Commons</a> (PDC)</b></li>
<li><b>The <a href="https://gdc.cancer.gov/">Genomic Data Commons</a> (GDC)</b></li>
<li><b>The <a href="https://datacommons.cancer.gov/repository/imaging-data-commons">Imaging Data Commons</a> (IDC)</b></li>
</ul> 
    
The CDA makes this data searchable in five main endpoints:

<ul>
<li><b>subject:</b> A patient entity captures the study-independent metadata for research subjects. Human research subjects are usually not traceable to a particular person to protect the subjects privacy.</li>
<li><b>researchsubject:</b> A research subject is the entity of interest in a specific research study or project, typically a human being or an animal, but can also be a device, group of humans or animals, or a tissue sample. Human research subjects are usually not traceable to a particular person to protect the subjects privacy. This entity plays the role of the case_id in existing data. An individual who participates in 3 studies will have 3 researchsubject IDs</li>
<li><b>specimen:</b> Any material taken as a sample from a biological entity (living or dead), or from a physical object or the environment. Specimens are usually collected as an example of their kind, often for use in some investigation.</li>
<li><b>file:</b> A unit of data about subjects, researchsubjects, specimens, or their associated information</li>
<li><b>mutation:</b> Molecular data about specific mutations, currently limited to the TCGA-READ project from GDC.</li>
</ul>
and two endpoints that offer deeper information about data in the researchsubject endpoint:
<ul>
<li><b>diagnosis:</b> A collection of characteristics that describe an abnormal condition of the body as assessed at a point in time. May be used to capture information about neoplastic and non-neoplastic conditions.</li>
<li><b>treatment:</b> Represent medication administration or other treatment types.</li>
</ul>
Any metadata field can be searched from any endpoint, the only difference between search types is what type of data is returned by default. This means that you can think of the CDA as a really, really enormous spreadsheet full of data. To search this enormous spreadsheet, you'd want select columns, and then filter rows.
</div>


## Finding Search Terms

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
   
   Accordingly, to see what search fields are available, Julia starts by using the command `columns`:

In [3]:
columns().to_dataframe()

fieldName   endpoint  \
0                    ALLELE_NUM   mutation   
1                      fileName   mutation   
2                          PICK   mutation   
3    subject_associated_project    subject   
4       days_to_treatment_start  treatment   
..                          ...        ...   
169                 Exon_Number   mutation   
170             normal_bam_uuid   mutation   
171                   MINIMISED   mutation   
172                       HGVSc   mutation   
173                      PUBMED   mutation   

                                           description     type      mode  
0    Allele number from input; 0 is reference, 1 is...   STRING  NULLABLE  
1      |-delimited list of name of underlying MAF file   STRING  NULLABLE  
2    Indicates if this block of consequence data wa...   STRING  NULLABLE  
3    The list of Projects associated with the Subject.   STRING  REPEATED  
4        The timepoint at which the treatment started.  INTEGER  NULLABLE  
..                                                 ...      ...       ...  
169              The exon number (out of total number)   STRING  NULLABLE  
170  Unique GDC identifier for the underlying norma...   STRING  NULLABLE  
171  Alleles in this variant have been converted to...   STRING  NULLABLE  
172  The coding sequence of the variant in HGVS rec...   STRING  NULLABLE  
173  Pubmed ID(s) of publications that cite existin...   STRING  NULLABLE  

[174 rows x 5 columns]

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
   
There are a lot of columns in the CDA data, but Julia is most interested in diagnosis data, so she searches the description column for "diagnosis":

In [4]:
columns().to_dataframe(search_fields=["description", "fieldName"],search_value="diagnosis")

fieldName         endpoint  \
0             age_at_diagnosis        diagnosis   
1  diagnosis_identifier_system        diagnosis   
2  primary_diagnosis_condition  researchsubject   
3          method_of_diagnosis        diagnosis   
4                 diagnosis_id        diagnosis   
5   diagnosis_identifier_value        diagnosis   
6       primary_diagnosis_site  researchsubject   
7            primary_diagnosis        diagnosis   

                                         description     type      mode  
0  The age in days of the individual at the time ...  INTEGER  NULLABLE  
1  The system or namespace that defines the ident...   STRING  NULLABLE  
2  The text term used to describe the type of mal...   STRING  NULLABLE  
3  The method used to confirm the subjects malign...   STRING  NULLABLE  
4  The 'logical' identifier of the entity in the ...   STRING  REQUIRED  
5  The value of the identifier, as defined by the...   STRING  NULLABLE  
6  The text term used to describe the primary sit...   STRING  NULLABLE  
7  The diagnosis instance that qualified a subjec...   STRING  NULLABLE

<div class="cdanote" style="background-color:#b3e5d5;color:black;padding:20px;">

To search the CDA, a user also needs to know what search terms are available. Each column will contain a huge amount of data, so retrieving all of the rows would be overwhelming. Instead, the CDA has a `unique_terms()` function that will return all of the unique values that populate the requested column. Like `columns`, `unique_terms` defaults to giving us an overview of the results, and can be filtered.
    
</div>

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Since Julia is interested specifically in uterine cancers, she looks for columns that appear to have anatomical data, and then uses the `unique_terms` function to see what data is available for 'ResearchSubject.Diagnosis.Treatment.treatment_anatomic_site' and 'ResearchSubject.primary_diagnosis_site' to see if 'uterine' appears, she uses the `show_counts` flag so she can also see how much data is associated with each term:

In [5]:
unique_terms("treatment_anatomic_site", show_counts = True).to_dataframe()

treatment_anatomic_site  Count
0                     Brain      5
1                    Cervix     87
2  Head - Face Or Neck, Nos      1
3  Lymph Node(s) Paraaortic     34
4                     Other      3
5                    Pelvis    102
6                     Spine      2
7                   Unknown    125

In [6]:
unique_terms("primary_diagnosis_site", show_counts = True).to_dataframe()

primary_diagnosis_site  Count
0                  Abdomen     92
1     Abdomen, Mediastinum    176
2          Abdomen, Pelvis    230
3           Adrenal Glands    271
4            Adrenal gland    851
..                     ...    ...
90             Uterus, NOS   2000
91                  Vagina     72
92                 Various    449
93  Various (11 locations)     89
94                   Vulva     10

[95 rows x 2 columns]

<div class="cdanote" style="background-color:#b3e5d5;color:black;padding:20px;">
    
CDA makes multiple datasets searchable from a common interface, but does not harmonize the data. This means that researchers should review all the terms in a column, and not just choose the first one that fits, as there may be other similar terms available as well.
    
</div>

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Julia sees that "treatment_anatomic_site" does not have 'Uterine', but does have 'Cervix'. She also notes that both 'Uterus' and 'Uterus, NOS' are listed in the "primary_diagnosis_site" results. As she was initially looking for "uterine", Julia decides to expand her search a bit to account for variable naming schemes. So, she runs a fuzzy match filter on the "ResearchSubject.primary_diagnosis_site" for 'uter' as that should cover all variants:

In [7]:
unique_terms("primary_diagnosis_site").to_list(filters="uter")

['Cervix uteri', 'Corpus uteri', 'Uterus', 'Uterus, NOS']

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Just to be sure, Julia also searches for any other instances of "cervix":

In [8]:
unique_terms("primary_diagnosis_site").to_list(filters="cerv")

['Cervix', 'Cervix uteri']

## Building a Query

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
With all her likely terms found, Julia begins to create a search that will get data for all of her terms. She does this by writing a series of `Q` statements that define what rows should be returned from each column. For the "treatment_anatomic_site", only one term is of interest, so she uses the `=` operator to get only exact matches:

In [9]:
Tsite = Q('treatment_anatomic_site = "Cervix"')

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
However, for "primary_diagnosis_site", Julia has several terms she wants to search with. Luckily, `Q` also can run fuzzy searches. It can also search more than one term at a time, so Julia writes one big `Q` statement to grab everything that is either 'uter' or 'cerv':

In [10]:
Dsite = Q('primary_diagnosis_site = "%uter%" OR primary_diagnosis_site = "%cerv%"')

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Finally, Julia adds her two queries together into one large one:

In [11]:
ALLDATA = Tsite.OR(Dsite)

## Looking at Summary Data

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Now that Julia has a query, she can use it to look for data in any of the CDA endpoints. She starts by getting an overall summary of what data is available using `count`:

In [12]:
ALLDATA.count.run()

Getting results from database

Total execution time: 0
                        min 44.665 sec 44665 ms

specimen_count : 41069

treatment_count : 3049

diagnosis_count : 3685

mutation_count : 903

researchsubject_count : 4869

subject_count : 3742

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
It seems there's a lot of data that might work for Julias study! Since she is interested in the beginings of cancer, she decides to start by looking at  the researchsubject information, since that is where most of the diagnosis information is. She again gets a summary using `count`:

In [13]:
ALLDATA.researchsubject.count.run()

Getting results from database

Total execution time: 0
                        min 7.838 sec 7838 ms

files : 322958

total : 4869

primary_diagnosis_condition 
 count 
 
 
 
 
 Adenomas and Adenocarcinomas 
 1672 
 
 
 Squamous Cell Neoplasms 
 609 
 
 
 Cystic, Mucinous and Serous Neoplasms 
 487 
 
 
 Uterine Corpus Endometrial Carcinoma 
 104 
 
 
 None 
 1175 
 
 
 Complex Mixed and Stromal Neoplasms 
 320 
 
 
 Myomatous Neoplasms 
 188 
 
 
 Epithelial Neoplasms, NOS 
 230 
 
 
 Not Reported 
 12 
 
 
 Complex Epithelial Neoplasms 
 27 
 
 
 Neuroepitheliomatous Neoplasms 
 1 
 
 
 Soft Tissue Tumors and Sarcomas, NOS 
 14 
 
 
 Mesonephromas 
 5 
 
 
 Neoplasms, NOS 
 12 
 
 
 Trophoblastic neoplasms 
 13 
 
 
 

 
 
 
 primary_diagnosis_site 
 count 
 
 
 
 
 Uterus, NOS 
 2000 
 
 
 Corpus uteri 
 780 
 
 
 Cervix uteri 
 915 
 
 
 Uterus 
 867 
 
 
 Cervix 
 307 
 
 
 

 
 
 
 researchsubject_identifier_system 
 count 
 
 
 
 
 GDC 
 3591 
 
 
 PDC 
 104 
 
 
 IDC 
 1174

## Refining Queries

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Browsing the primary_diagnosis_condition data, Julia notices that there are a large number of research subjects that are Adenomas and Adenocarcinomas. Since Julia wants to look for common phenotypes in early cancers, she decides it might be easier to exclude the endocrine related data, as they might have different mechanisms. So she adds a new filter to her query:

In [14]:
Noadeno = Q('primary_diagnosis_condition != "Adenomas and Adenocarcinomas"')

NoAdenoData = ALLDATA.AND(Noadeno)

NoAdenoData.researchsubject.count.run()

Getting results from database

Total execution time: 0
                        min 7.824 sec 7824 ms

files : 297379

total : 3197

primary_diagnosis_condition 
 count 
 
 
 
 
 Myomatous Neoplasms 
 188 
 
 
 Uterine Corpus Endometrial Carcinoma 
 104 
 
 
 Cystic, Mucinous and Serous Neoplasms 
 487 
 
 
 Squamous Cell Neoplasms 
 609 
 
 
 Complex Mixed and Stromal Neoplasms 
 320 
 
 
 None 
 1175 
 
 
 Epithelial Neoplasms, NOS 
 230 
 
 
 Soft Tissue Tumors and Sarcomas, NOS 
 14 
 
 
 Mesonephromas 
 5 
 
 
 Neoplasms, NOS 
 12 
 
 
 Trophoblastic neoplasms 
 13 
 
 
 Complex Epithelial Neoplasms 
 27 
 
 
 Not Reported 
 12 
 
 
 Neuroepitheliomatous Neoplasms 
 1 
 
 
 

 
 
 
 primary_diagnosis_site 
 count 
 
 
 
 
 Corpus uteri 
 373 
 
 
 Uterus, NOS 
 962 
 
 
 Cervix uteri 
 688 
 
 
 Uterus 
 867 
 
 
 Cervix 
 307 
 
 
 

 
 
 
 researchsubject_identifier_system 
 count 
 
 
 
 
 GDC 
 1919 
 
 
 PDC 
 104 
 
 
 IDC 
 1174

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
She then previews the actual metadata for researchsubject, subject, and file, to make sure that they have all the information she will need for her work. Since she's mostly interested in looking at the kinds of data available from each endpoint:

In [15]:
NoAdenoData.researchsubject.run().to_dataframe() # view the dataframe

Getting results from database

Total execution time: 0
                        min 4.19 sec 4190 ms

researchsubject_id  \
0   03b6910a-f8f1-43cf-afe8-8b9ea2687b26   
1   2317cb92-3406-4974-a2ce-04307b17fc52   
2   2e08a89e-4035-4782-b54f-f98eef5db80d   
3   31187375-5a0a-4e60-837b-cd5395a6971e   
4   3223fec6-1d35-419a-8ee9-7c5885b8be1e   
..                                   ...   
95               TCGA-VS-A9UH__tcga_cesc   
96  a307e88b-745c-469e-ba24-a7cc544e8859   
97  d4510801-8ce4-4f10-8b31-25c0a39b5135   
98  d9952e44-b573-4854-893e-b3bbc5287f2f   
99  de4e13c8-5ad0-46d2-ae54-b9ca22b939d8   

                           researchsubject_identifier  \
0   [{'system': 'GDC', 'value': '03b6910a-f8f1-43c...   
1   [{'system': 'GDC', 'value': '2317cb92-3406-497...   
2   [{'system': 'GDC', 'value': '2e08a89e-4035-478...   
3   [{'system': 'GDC', 'value': '31187375-5a0a-4e6...   
4   [{'system': 'GDC', 'value': '3223fec6-1d35-419...   
..                                                ...   
95  [{'system': 'IDC', 'value': 'TCGA-VS-A9UH__tcg...   
96  [{'system': 'GDC', 'value': 'a307e88b-745c-469...   
97  [{'system': 'GDC', 'value': 'd4510801-8ce4-4f1...   
98  [{'system': 'GDC', 'value': 'd9952e44-b573-485...   
99  [{'system': 'GDC', 'value': 'de4e13c8-5ad0-46d...   

   member_of_research_project            primary_diagnosis_condition  \
0                   GENIE-MSK              Epithelial Neoplasms, NOS   
1                   GENIE-MSK    Complex Mixed and Stromal Neoplasms   
2                   TCGA-CESC                Squamous Cell Neoplasms   
3                   GENIE-MSK           Complex Epithelial Neoplasms   
4                   TCGA-CESC                Squamous Cell Neoplasms   
..                        ...                                    ...   
95                  tcga_cesc                                   None   
96                 GENIE-DFCI    Complex Mixed and Stromal Neoplasms   
97                  TCGA-CESC                Squamous Cell Neoplasms   
98                   TCGA-UCS    Complex Mixed and Stromal Neoplasms   
99                  TCGA-UCEC  Cystic, Mucinous and Serous Neoplasms   

   primary_diagnosis_site           subject_id  
0            Corpus uteri  GENIE-MSK-P-0018443  
1             Uterus, NOS  GENIE-MSK-P-0018286  
2            Cervix uteri         TCGA-VS-A8EJ  
3            Cervix uteri  GENIE-MSK-P-0001655  
4            Cervix uteri         TCGA-LP-A4AX  
..                    ...                  ...  
95                 Cervix         TCGA-VS-A9UH  
96           Corpus uteri    GENIE-DFCI-023832  
97           Cervix uteri         TCGA-EK-A2R8  
98            Uterus, NOS         TCGA-N5-A4RD  
99           Corpus uteri         TCGA-EO-A1Y8  

[100 rows x 6 columns]

---

<div class="cdadefine" style="background-color:#add9e5;color:black;padding:20px;">

<h3>ResearchSubject Field Definitions</h3>

<i>A research subject is the entity of interest in a specific research study or project, typically a human being or an animal, but can also be a device, group of humans or animals, or a tissue sample. Human research subjects are usually not traceable to a particular person to protect the subjects privacy. This entity plays the role of the case_id in existing data. An individual who participates in 3 studies will have 3 researchsubject IDs</i>
    
<ul>
<li><b>id:</b> The 'logical' identifier of the entity in the system of record, e.g. a UUID. This 'id' is unique within a given system. The identified entity may have a different 'id' in a different system. For CDA, this is case_id.</li>
<li><b>identifier:</b> A 'business' identifier for the entity, typically as provided by an external system or authority, that persists across implementing systems (i.e. a 'logical' identifier). Uses a specialized, complex 'Identifier' data type to capture information about the source of the business identifier - or a URI expressed as a string to an existing entity.</li>
<li><b>identifier.system:</b> The system or namespace that defines the identifier.</li>
<li><b>identifier.value:</b> The value of the identifier, as defined by the system.</li>
<li><b>member_of_research_project:</b> A reference to the Study(s) of which this ResearchSubject is a member.</li>
<li><b>primary_diagnosis_condition:</b> The text term used to describe the type of malignant disease, as categorized by the World Health Organization's (WHO) <a href="https://www.who.int/standards/classifications/other-classifications/international-classification-of-diseases-for-oncology">International Classification of Diseases for Oncology</a> (ICD-O). This attribute represents the disease that qualified the subject for inclusion on the ResearchProject.</li>
<li><b>primary_diagnosis_site:</b> The text term used to describe the primary site of disease, as categorized by the World Health Organization's (WHO) <a href="https://www.who.int/standards/classifications/other-classifications/international-classification-of-diseases-for-oncology">International Classification of Diseases for Oncology</a> (ICD-O). This categorization groups cases into general categories. This attribute represents the primary site of disease that qualified the subject for inclusion on the ResearchProject.</li>
<li><b>subject_id:</b> The 'logical' identifier of the entity in the system of record, e.g. a UUID. This 'id' is unique within a given system. The identified entity may have a different 'id' in a different system. Can be joined to the `id` field from subject results</li>
</ul>  

</div>
    
---

In [16]:
NoAdenoData.subject.run().to_dataframe() # view the dataframe

Getting results from database

Total execution time: 0
                        min 4.263 sec 4263 ms

subject_id                                 subject_identifier  \
0        AD10485            [{'system': 'GDC', 'value': 'AD10485'}]   
1        AD17572            [{'system': 'GDC', 'value': 'AD17572'}]   
2         AD6453             [{'system': 'GDC', 'value': 'AD6453'}]   
3         AD6896             [{'system': 'GDC', 'value': 'AD6896'}]   
4      C3L-00586  [{'system': 'GDC', 'value': 'C3L-00586'}, {'sy...   
..           ...                                                ...   
95  TCGA-EY-A1GP  [{'system': 'GDC', 'value': 'TCGA-EY-A1GP'}, {...   
96  TCGA-FI-A2D2  [{'system': 'GDC', 'value': 'TCGA-FI-A2D2'}, {...   
97  TCGA-N9-A4PZ  [{'system': 'GDC', 'value': 'TCGA-N9-A4PZ'}, {...   
98  TCGA-PG-A6IB  [{'system': 'GDC', 'value': 'TCGA-PG-A6IB'}, {...   
99  TCGA-VS-A8QC  [{'system': 'GDC', 'value': 'TCGA-VS-A8QC'}, {...   

         species     sex                       race               ethnicity  \
0   homo sapiens  female               not reported            not reported   
1   homo sapiens  female               not reported            not reported   
2   homo sapiens  female               not reported            not reported   
3   homo sapiens  female               not reported            not reported   
4   homo sapiens  female                      white  not hispanic or latino   
..           ...     ...                        ...                     ...   
95  homo sapiens  female  black or african american  not hispanic or latino   
96  homo sapiens  female                      white  not hispanic or latino   
97  homo sapiens  female                      white            not reported   
98  homo sapiens  female  black or african american  not hispanic or latino   
99  homo sapiens  female                      white            not reported   

    days_to_birth               subject_associated_project  vital_status  \
0             NaN                                  [FM-AD]  Not Reported   
1             NaN                                  [FM-AD]  Not Reported   
2             NaN                                  [FM-AD]  Not Reported   
3             NaN                                  [FM-AD]  Not Reported   
4        -18580.0  [CPTAC-3, cptac_ucec, CPTAC3-Discovery]         Alive   
..            ...                                      ...           ...   
95            NaN                   [TCGA-UCEC, tcga_ucec]         Alive   
96            NaN                   [TCGA-UCEC, tcga_ucec]          Dead   
97            NaN                     [TCGA-UCS, tcga_ucs]          Dead   
98            NaN                   [TCGA-UCEC, tcga_ucec]         Alive   
99            NaN                   [TCGA-CESC, tcga_cesc]          Dead   

   days_to_death cause_of_death  
0           None           None  
1           None           None  
2           None           None  
3           None           None  
4           None   Not Reported  
..           ...            ...  
95          None           None  
96          None           None  
97          None           None  
98          None           None  
99          None           None  

[100 rows x 11 columns]

---

<div class="cdadefine" style="background-color:#add9e5;color:black;padding:20px;">

<h3>Subject Field Definitions</h3>

<i>A patient entity captures the study-independent metadata for research subjects. Human research subjects are usually not traceable to a particular person to protect the subjects privacy.</i>

    
<ul>
<li><b>id:</b> The 'logical' identifier of the entity in the system of record, e.g. a UUID. This 'id' is unique within a given system. The identified entity may have a different 'id' in a different system.",STRING</li>
<li><b>identifier:</b> A 'business' identifier for the entity, typically as provided by an external system or authority, that persists across implementing systems (i.e. a 'logical' identifier). Uses a specialized, complex 'Identifier' data type to capture information about the source of the business identifier - or a URI expressed as a string to an existing entity.</li>
<li><b>identifier.system:</b> The system or namespace that defines the identifier.</li>
<li><b>identifier.value:</b> The value of the identifier, as defined by the system.</li>
<li><b>species:</b> The taxonomic group (e.g. species) of the patient. For MVP, since taxonomy vocabulary is consistent between GDC and PDC, using text. Ultimately, this will be a term returned by the vocabulary service.</li>
<li><b>sex:</b> The biologic character or quality that distinguishes male and female from one another as expressed by analysis of the person's gonadal, morphologic (internal and external), chromosomal, and hormonal characteristics.</li>
<li><b>race:</b> An arbitrary classification of a taxonomic group that is a division of a species. It usually arises as a consequence of geographical isolation within a species and is characterized by shared heredity, physical attributes and behavior, and in the case of humans, by common history, nationality, or geographic distribution. The provided values are based on the categories defined by the U.S. Office of Management and Business and used by the U.S. Census Bureau.</li>
<li><b>ethnicity:</b> An individual's self-described social and cultural grouping, specifically whether an individual describes themselves as Hispanic or Latino. The provided values are based on the categories defined by the U.S. Office of Management and Business and used by the U.S. Census Bureau.</li>
<li><b>days_to_birth:</b> Number of days between the date used for index and the date from a person's date of birth represented as a calculated negative number of days.</li>
<li><b>subject_associated_project:</b> The list of Projects associated with the Subject.</li>
<li><b>vital_status:</b> Coded value indicating the state or condition of being living or deceased; also includes the case where the vital status is unknown.</li>
<li><b>days_to_death:</b> Number of days between the date used for index and the date from a person's date of death represented as a calculated number of days.</li>
<li><b>cause_of_death:</b> Coded value indicating the circumstance or condition that results in the death of the subject.</li>
</ul>  

</div>
    
---

In [17]:
NoAdenoData.subject.file.run().to_dataframe() # view the dataframe

Getting results from database

Total execution time: 0
                        min 13.387 sec 13387 ms

file_id  \
0   067a1e40-3b7f-4058-863e-c3f246e80029   
1   073249ac-a3ea-46ca-a89e-82e26e3582ce   
2   192273a6-3485-450b-a596-33ee9c67cd59   
3   1b99980e-9ea2-4101-94eb-2edcff38b2e3   
4   28649881-c6cb-419b-a5cf-ec596cc007c0   
..                                   ...   
95  2cf0dee5-0306-4b7e-b895-4cdcdd5d3520   
96  3bf04ede-73ab-4637-9bec-17303d6c9072   
97  467d743f-af87-4248-9de0-732821f03b0f   
98  54f5b813-cfe4-4aae-9124-99f82043f546   
99  57b94fd1-a8a0-4879-8647-1947c742ea4c   

                                      file_identifier  \
0   [{'system': 'GDC', 'value': '067a1e40-3b7f-405...   
1   [{'system': 'IDC', 'value': '073249ac-a3ea-46c...   
2   [{'system': 'GDC', 'value': '192273a6-3485-450...   
3   [{'system': 'IDC', 'value': '1b99980e-9ea2-410...   
4   [{'system': 'GDC', 'value': '28649881-c6cb-419...   
..                                                ...   
95  [{'system': 'GDC', 'value': '2cf0dee5-0306-4b7...   
96  [{'system': 'IDC', 'value': '3bf04ede-73ab-463...   
97  [{'system': 'GDC', 'value': '467d743f-af87-424...   
98  [{'system': 'GDC', 'value': '54f5b813-cfe4-4aa...   
99  [{'system': 'GDC', 'value': '57b94fd1-a8a0-487...   

                                                label  \
0   091bd25a-a6f0-4b2b-bd52-d08405b662ca.genie.ali...   
1            073249ac-a3ea-46ca-a89e-82e26e3582ce.dcm   
2   55c118ac-28ef-4c05-b0c2-42520fcb62cd.genie.ali...   
3            1b99980e-9ea2-4101-94eb-2edcff38b2e3.dcm   
4   e1a62968-df48-425e-831f-59470d37ce9f.targeted_...   
..                                                ...   
95  f658ff92-8cc4-4f07-9cbf-7f9c9544db73.targeted_...   
96           3bf04ede-73ab-4637-9bec-17303d6c9072.dcm   
97  b03017a8-dd14-48cd-96e2-70d1a623f240.genie.ali...   
98  4418d94c-a2c6-4066-87ef-4417c6bb44be.genie.ali...   
99  080496d4-9f5b-4c94-887f-6ab9fece68d9.targeted_...   

                  data_category                          data_type  \
0   Simple Nucleotide Variation  Masked Annotated Somatic Mutation   
1                       Imaging                               None   
2         Copy Number Variation      Gene Level Copy Number Scores   
3                       Imaging                               None   
4   Simple Nucleotide Variation        Raw Simple Somatic Mutation   
..                          ...                                ...   
95  Simple Nucleotide Variation        Aggregated Somatic Mutation   
96                      Imaging                               None   
97        Copy Number Variation      Gene Level Copy Number Scores   
98  Simple Nucleotide Variation  Masked Annotated Somatic Mutation   
99  Simple Nucleotide Variation        Aggregated Somatic Mutation   

   file_format file_associated_project  \
0          MAF             [GENIE-MSK]   
1        DICOM              [tcga_ucs]   
2          TSV            [GENIE-DFCI]   
3        DICOM              [tcga_ucs]   
4          VCF                 [FM-AD]   
..         ...                     ...   
95         MAF                 [FM-AD]   
96       DICOM              [tcga_ucs]   
97         TSV            [GENIE-DFCI]   
98         MAF             [GENIE-MSK]   
99         MAF                 [FM-AD]   

                                              drs_uri  byte_size  \
0   drs://dg.4DFC:067a1e40-3b7f-4058-863e-c3f246e8...     1707.0   
1   drs://dg.4DFC:073249ac-a3ea-46ca-a89e-82e26e35...        NaN   
2   drs://dg.4DFC:192273a6-3485-450b-a596-33ee9c67...    22910.0   
3   drs://dg.4DFC:1b99980e-9ea2-4101-94eb-2edcff38...        NaN   
4   drs://dg.4DFC:28649881-c6cb-419b-a5cf-ec596cc0...     1142.0   
..                                                ...        ...   
95  drs://dg.4DFC:2cf0dee5-0306-4b7e-b895-4cdcdd5d...     2989.0   
96  drs://dg.4DFC:3bf04ede-73ab-4637-9bec-17303d6c...        NaN   
97  drs://dg.4DFC:467d743f-af87-4248-9de0-732821f0...    22910.0   
98  drs://dg.4DFC:54f5b813-cfe4-4aae-9124-99f82043...     4228.0   
99  drs://dg.4DFC:57b94fd1-a8a0-4879-864


---

<div class="cdadefine" style="background-color:#add9e5;color:black;padding:20px;">

<h3>File Field Definitions</h3>

<i>A file is an information-bearing electronic object that contains a physical embodiment of some information using a particular character encoding.</i>

    
<ul>
  <li><b>id:</b> The 'logical' identifier of the entity in the system of record, e.g. a UUID. This 'id' is unique within a given system. The identified entity may have a different 'id' in a different system.</li>
<li><b>identifier:</b> A 'business' identifier for the entity, typically as provided by an external system or authority, that persists across implementing systems (i.e. a 'logical' identifier). Uses a specialized, complex 'Identifier' data type to capture information about the source of the business identifier - or a URI expressed as a string to an existing entity.</li>
<li><b>identifier.system:</b> The system or namespace that defines the identifier.</li>
<li><b>identifier.value:</b> The value of the identifier, as defined by the system.</li>
  <li><b>label:</b> Short name or abbreviation for dataset. Maps to rdfs:label.</li>
  <li><b>data_catagory:</b> Broad categorization of the contents of the data file.</li>
  <li><b>data_type:</b> Specific content type of the data file.</li>
  <li><b>file_format:</b> Format of the data files.</li>
  <li><b>associated_project:</b> A reference to the Project(s) of which this ResearchSubject is a member. The associated_project may be embedded using the ref definition or may be a reference to the id for the Project - or a URI expressed as a string to an existing entity.</li>
  <li><b>drs_uri:</b> A string of characters used to identify a resource on the Data Repo Service(DRS). Can be used to retrieve this specific file from a server.</li>
  <li><b>byte_size:</b> Size of the file in bytes. Maps to dcat:byteSize.</li>
  <li><b>checksum:</b> The md5 value for the file. A digit representing the sum of the correct digits in a piece of stored or transmitted digital data, against which later comparisons can be made to detect errors in the data.</li>
  <li><b>data_modality:</b> Data modality describes the biological nature of the information gathered as the result of an Activity, independent of the technology or methods used to produce the information. Always one of "Genomic", "Proteomic", or "Imaging".</li>
  <li><b>imaging_modality:</b> An imaging modality describes the imaging equipment and/or method used to acquire certain structural or functional information about the body. These include but are not limited to computed tomography (CT) and magnetic resonance imaging (MRI). Taken from the DICOM standard.</li>
  <li><b>dbgap_accession_number:</b> The dbgap accession number for the project.</li>
</ul>  

</div>
    
---


## Working with Results (pagination)

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Finally, Julia wants to save these results to use for the future. Since the preview dataframes only show the first 100 results of each search, she uses the `paginator` function to get all the data from the subject and researchsubject endpoints into their own dataframes:

In [18]:
researchsubs = NoAdenoData.researchsubject.run()
rsdf = researchsubs.auto_paginator(to_df=True)

Getting results from database

Total execution time: 0
                        min 3.703 sec 3703 ms

Output()

In [19]:
subs = NoAdenoData.subject.run()
subsdf = subs.auto_paginator(to_df=True)

Getting results from database

Total execution time: 0
                        min 3.642 sec 3642 ms

Output()

In [20]:
rsdf # view the researchsubject dataframe

researchsubject_id  \
0   d6929fe7-908d-4684-b799-1c7d1bfe4835   
1   e9de2706-246c-46ae-a48c-7cb9bff7e723   
2   0cabe364-1e30-433d-b301-3fcffd953b09   
3   14c744c0-1ae8-4d8b-bb7c-6149019dc1a3   
4   164241df-c75b-482d-ad6a-84b0ee9aaf66   
..                                   ...   
95               TCGA-VS-A9UH__tcga_cesc   
96  a307e88b-745c-469e-ba24-a7cc544e8859   
97  d4510801-8ce4-4f10-8b31-25c0a39b5135   
98  d9952e44-b573-4854-893e-b3bbc5287f2f   
99  de4e13c8-5ad0-46d2-ae54-b9ca22b939d8   

                           researchsubject_identifier  \
0   [{'system': 'GDC', 'value': 'd6929fe7-908d-468...   
1   [{'system': 'GDC', 'value': 'e9de2706-246c-46a...   
2   [{'system': 'GDC', 'value': '0cabe364-1e30-433...   
3   [{'system': 'GDC', 'value': '14c744c0-1ae8-4d8...   
4   [{'system': 'GDC', 'value': '164241df-c75b-482...   
..                                                ...   
95  [{'system': 'IDC', 'value': 'TCGA-VS-A9UH__tcg...   
96  [{'system': 'GDC', 'value': 'a307e88b-745c-469...   
97  [{'system': 'GDC', 'value': 'd4510801-8ce4-4f1...   
98  [{'system': 'GDC', 'value': 'd9952e44-b573-485...   
99  [{'system': 'GDC', 'value': 'de4e13c8-5ad0-46d...   

   member_of_research_project            primary_diagnosis_condition  \
0                   GENIE-MSK                    Myomatous Neoplasms   
1                  GENIE-DFCI              Epithelial Neoplasms, NOS   
2                       FM-AD  Cystic, Mucinous and Serous Neoplasms   
3                   GENIE-UHN              Epithelial Neoplasms, NOS   
4                  GENIE-DFCI    Complex Mixed and Stromal Neoplasms   
..                        ...                                    ...   
95                  tcga_cesc                                   None   
96                 GENIE-DFCI    Complex Mixed and Stromal Neoplasms   
97                  TCGA-CESC                Squamous Cell Neoplasms   
98                   TCGA-UCS    Complex Mixed and Stromal Neoplasms   
99                  TCGA-UCEC  Cystic, Mucinous and Serous Neoplasms   

   primary_diagnosis_site           subject_id  
0             Uterus, NOS  GENIE-MSK-P-0003754  
1            Corpus uteri    GENIE-DFCI-036994  
2             Uterus, NOS              AD10783  
3            Corpus uteri     GENIE-UHN-944776  
4            Corpus uteri    GENIE-DFCI-009119  
..                    ...                  ...  
95                 Cervix         TCGA-VS-A9UH  
96           Corpus uteri    GENIE-DFCI-023832  
97           Cervix uteri         TCGA-EK-A2R8  
98            Uterus, NOS         TCGA-N5-A4RD  
99           Corpus uteri         TCGA-EO-A1Y8  

[3197 rows x 6 columns]

In [21]:
subsdf # view the subject dataframe

subject_id                                 subject_identifier  \
0   HTMCP-03-06-02146  [{'system': 'GDC', 'value': 'HTMCP-03-06-02146'}]   
1        TCGA-AX-A0IU  [{'system': 'GDC', 'value': 'TCGA-AX-A0IU'}, {...   
2        TCGA-AX-A1C5  [{'system': 'GDC', 'value': 'TCGA-AX-A1C5'}, {...   
3        TCGA-AX-A1CA  [{'system': 'GDC', 'value': 'TCGA-AX-A1CA'}, {...   
4        TCGA-AX-A1CF  [{'system': 'GDC', 'value': 'TCGA-AX-A1CF'}, {...   
..                ...                                                ...   
95       TCGA-EY-A1GP  [{'system': 'GDC', 'value': 'TCGA-EY-A1GP'}, {...   
96       TCGA-FI-A2D2  [{'system': 'GDC', 'value': 'TCGA-FI-A2D2'}, {...   
97       TCGA-N9-A4PZ  [{'system': 'GDC', 'value': 'TCGA-N9-A4PZ'}, {...   
98       TCGA-PG-A6IB  [{'system': 'GDC', 'value': 'TCGA-PG-A6IB'}, {...   
99       TCGA-VS-A8QC  [{'system': 'GDC', 'value': 'TCGA-VS-A8QC'}, {...   

         species     sex                       race               ethnicity  \
0   homo sapiens  female  black or african american  not hispanic or latino   
1   homo sapiens  female  black or african american  not hispanic or latino   
2   homo sapiens  female                      white  not hispanic or latino   
3   homo sapiens  female  black or african american  not hispanic or latino   
4   homo sapiens  female                      white  not hispanic or latino   
..           ...     ...                        ...                     ...   
95  homo sapiens  female  black or african american  not hispanic or latino   
96  homo sapiens  female                      white  not hispanic or latino   
97  homo sapiens  female                      white            not reported   
98  homo sapiens  female  black or african american  not hispanic or latino   
99  homo sapiens  female                      white            not reported   

    days_to_birth subject_associated_project vital_status days_to_death  \
0             NaN            [CGCI-HTMCP-CC]         Dead          None   
1             NaN     [TCGA-UCEC, tcga_ucec]        Alive          None   
2             NaN     [TCGA-UCEC, tcga_ucec]        Alive          None   
3             NaN     [TCGA-UCEC, tcga_ucec]        Alive          None   
4             NaN     [TCGA-UCEC, tcga_ucec]        Alive          None   
..            ...                        ...          ...           ...   
95            NaN     [TCGA-UCEC, tcga_ucec]        Alive           NaN   
96            NaN     [TCGA-UCEC, tcga_ucec]         Dead           NaN   
97            NaN       [TCGA-UCS, tcga_ucs]         Dead           NaN   
98            NaN     [TCGA-UCEC, tcga_ucec]        Alive           NaN   
99            NaN     [TCGA-CESC, tcga_cesc]         Dead           NaN   

   cause_of_death  
0            None  
1            None  
2            None  
3            None  
4            None  
..            ...  
95           None  
96           None  
97           None  
98           None  
99           None  

[2609 rows x 11 columns]

## Merging Results across Endpoints

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Then Julia uses the `subject_id` and `id` fields in each result to merge them together into one big dataset. She also specifies that any columns that are in both tables should be kept and have a suffix added to their name. This will help her to check that her merge worked correctly:

In [22]:
allmetadata = pd.merge(rsdf,
                subsdf,
                left_on="subject_id",
                right_on='subject_id',
                suffixes=("_rs", "_sub"))

allmetadata

researchsubject_id  \
0     d6929fe7-908d-4684-b799-1c7d1bfe4835   
1     e9de2706-246c-46ae-a48c-7cb9bff7e723   
2     0cabe364-1e30-433d-b301-3fcffd953b09   
3     14c744c0-1ae8-4d8b-bb7c-6149019dc1a3   
4     164241df-c75b-482d-ad6a-84b0ee9aaf66   
...                                    ...   
3192  829273bb-eb58-4c6f-b192-599344f5b1ed   
3193  92086136-3281-4ce9-a2df-4b597aaf22c8   
3194                 C3N-01766__cptac_ucec   
3195               TCGA-AX-A2H7__tcga_ucec   
3196  a307e88b-745c-469e-ba24-a7cc544e8859   

                             researchsubject_identifier  \
0     [{'system': 'GDC', 'value': 'd6929fe7-908d-468...   
1     [{'system': 'GDC', 'value': 'e9de2706-246c-46a...   
2     [{'system': 'GDC', 'value': '0cabe364-1e30-433...   
3     [{'system': 'GDC', 'value': '14c744c0-1ae8-4d8...   
4     [{'system': 'GDC', 'value': '164241df-c75b-482...   
...                                                 ...   
3192  [{'system': 'GDC', 'value': '829273bb-eb58-4c6...   
3193  [{'system': 'GDC', 'value': '92086136-3281-4ce...   
3194  [{'system': 'IDC', 'value': 'C3N-01766__cptac_...   
3195  [{'system': 'IDC', 'value': 'TCGA-AX-A2H7__tcg...   
3196  [{'system': 'GDC', 'value': 'a307e88b-745c-469...   

     member_of_research_project            primary_diagnosis_condition  \
0                     GENIE-MSK                    Myomatous Neoplasms   
1                    GENIE-DFCI              Epithelial Neoplasms, NOS   
2                         FM-AD  Cystic, Mucinous and Serous Neoplasms   
3                     GENIE-UHN              Epithelial Neoplasms, NOS   
4                    GENIE-DFCI    Complex Mixed and Stromal Neoplasms   
...                         ...                                    ...   
3192                  GENIE-MSK           Complex Epithelial Neoplasms   
3193                  GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
3194                 cptac_ucec                                   None   
3195                  tcga_ucec                                   None   
3196                 GENIE-DFCI    Complex Mixed and Stromal Neoplasms   

     primary_diagnosis_site           subject_id  \
0               Uterus, NOS  GENIE-MSK-P-0003754   
1              Corpus uteri    GENIE-DFCI-036994   
2               Uterus, NOS              AD10783   
3              Corpus uteri     GENIE-UHN-944776   
4              Corpus uteri    GENIE-DFCI-009119   
...                     ...                  ...   
3192           Cervix uteri  GENIE-MSK-P-0008316   
3193           Cervix uteri       GENIE-NKI-3GI3   
3194                 Uterus            C3N-01766   
3195                 Uterus         TCGA-AX-A2H7   
3196           Corpus uteri    GENIE-DFCI-023832   

                                     subject_identifier       species     sex  \
0     [{'system': 'GDC', 'value': 'GENIE-MSK-P-00037...  homo sapiens  female   
1     [{'system': 'GDC', 'value': 'GENIE-DFCI-036994'}]  homo sapiens  female   
2               [{'system': 'GDC', 'value': 'AD10783'}]  homo sapiens  female   
3      [{'system': 'GDC', 'value': 'GENIE-UHN-944776'}]  homo sapiens  female   
4     [{'system': 'GDC', 'value': 'GENIE-DFCI-009119'}]  homo sapiens  female   
...                                                 ...           ...     ...   
3192  [{'system': 'GDC', 'value': 'GENIE-MSK-P-00083...  homo sapiens  female   
3193     [{'system': 'GDC', 'value': 'GENIE-NKI-3GI3'}]  homo sapiens    male   
3194          [{'system': 'IDC', 'value': 'C3N-01766'}]  homo sapiens    None   
3195  [{'system': 'GDC', 'value': 'TCGA-AX-A2H7'}, {...  homo sapiens  female   
3196  [{'system': 'GDC', 'value': 'GENIE-DFCI-023832'}]  homo sapiens  female   

              race               ethnicity  days_to_birth  \
0            white  not hispanic or latino            NaN   
1            white  not hispanic or latino            NaN   
2     not reported            not reported            NaN   
3            asian  not allowed

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
`subject_id` from the research subject results seems to perfectly match the id data from the subject table, `id_sub`. Julia then checks to see that her dataframe is the right size. She had 3197 researchsubject rows, so she expects 3197 rows here as well:

In [23]:
allmetadata.count()

researchsubject_id             3197
researchsubject_identifier     3197
member_of_research_project     3197
primary_diagnosis_condition    2022
primary_diagnosis_site         3197
subject_id                     3197
subject_identifier             3197
species                        3197
sex                            3025
race                           3025
ethnicity                      3025
days_to_birth                   206
subject_associated_project     3197
vital_status                   3025
days_to_death                    22
cause_of_death                  206
dtype: int64

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Satisfied with her results, Julia saves the data out to a csv so she can browse it with Excel:

In [24]:
allmetadata.to_csv("allmetadata.csv")

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Julia knows from her subject count summary that there are more than 200,000 files associated with her subjects, which is likely far more than she needs. To help her decide what files she wants, Julia uses endpoint chaining to get summary information about the files that are assigned to researchsubjects for her search criteria:


In [25]:
NoAdenoData.researchsubject.file.count.run()

Getting results from database

Total execution time: 0
                        min 7.554 sec 7554 ms

total : 297379

data_category 
 count 
 
 
 
 
 Imaging 
 265303 
 
 
 Transcriptome Profiling 
 2820 
 
 
 Biospecimen 
 2866 
 
 
 Peptide Spectral Matches 
 1280 
 
 
 Processed Mass Spectra 
 640 
 
 
 Simple Nucleotide Variation 
 9987 
 
 
 Raw Mass Spectra 
 640 
 
 
 Copy Number Variation 
 4079 
 
 
 Structural Variation 
 2192 
 
 
 Clinical 
 774 
 
 
 DNA Methylation 
 1947 
 
 
 Sequencing Reads 
 4142 
 
 
 Somatic Structural Variation 
 370 
 
 
 Proteome Profiling 
 339 
 
 
 

 
 
 
 data_type 
 count 
 
 
 
 
 None 
 265303 
 
 
 Proprietary 
 640 
 
 
 Open Standard 
 1280 
 
 
 Masked Annotated Somatic Mutation 
 1024 
 
 
 Transcript Fusion 
 2278 
 
 
 Annotated Somatic Mutation 
 4871 
 
 
 Text 
 640 
 
 
 Masked Copy Number Segment 
 998 
 
 
 Gene Level Copy Number 
 637 
 
 
 Slide Image 
 1111 
 
 
 Aligned Reads 
 4142 
 
 
 Biospecimen Supplement 
 1755 
 
 
 Structural Rearrangement 
 284 
 
 
 Clinical Supplement 
 773 
 
 
 Raw Simple Somatic Mutation 
 2811 
 
 
 Masked Intensities 
 1298 
 
 
 Copy Number Segment 
 1140 
 
 
 Aggregated Somatic Mutation 
 732 
 
 
 Isoform Expression Quantification 
 700 
 
 
 Methylation Beta Value 
 649 
 
 
 Gene Expression Quantification 
 710 
 
 
 Gene Level Copy Number Scores 
 809 
 
 
 Protein Expression Quantification 
 339 
 
 
 Splice Junction Quantification 
 710 
 
 
 miRNA Expression Quantification 
 700 
 
 
 Allele-specific Copy Number Segment 
 495 
 
 
 Masked Somatic Mutation 
 549 
 
 
 Pathology Report 
 1 
 
 
 

 
 
 
 file_format 
 count 
 
 
 
 
 DICOM 
 265303 
 
 
 vendor-specific 
 640 
 
 
 BAM 
 4142 
 
 
 VCF 
 5480 
 
 
 tsv 
 640 
 
 
 BCR Biotab 
 76 
 
 
 TSV 
 3980 
 
 
 mzML 
 640 
 
 
 TXT 
 4827 
 
 
 BCR SSF XML 
 517 
 
 
 MAF 
 4649 
 
 
 SVS 
 1111 
 
 
 BEDPE 
 1504 
 
 
 mzIdentML 
 640 
 
 
 BCR XML 
 1217 
 
 
 BCR PPS XML 
 193 
 
 
 IDAT 
 1298 
 
 
 CDC JSON 
 1 
 
 
 BCR Auxiliary XML 
 474 
 
 
 BCR OMF XML 
 39 
 
 
 XLSX 
 7 
 
 
 PDF 
 1 
 
 
 

 
 
 
 file_identifier_system 
 count 
 
 
 
 
 IDC 
 265303 
 
 
 GDC 
 29516 
 
 
 PDC 
 2560

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
    
Julia decides that a good place to start would be with Slide Images. There's only 1111, so she should be able to quickly scan through them over the next few days and see if they will be useful. So she adds one more filter on her search:

In [26]:
JustSlides = Q('data_type = "Slide Image"')
NoadenoJustSlides = NoAdenoData.AND(JustSlides)
NoadenoJustSlides.researchsubject.file.count.run()

Getting results from database

Total execution time: 0
                        min 7.392 sec 7392 ms

total : 1111

data_category 
 count 
 
 
 
 
 Biospecimen 
 1111 
 
 
 

 
 
 
 data_type 
 count 
 
 
 
 
 Slide Image 
 1111 
 
 
 

 
 
 
 file_format 
 count 
 
 
 
 
 SVS 
 1111 
 
 
 

 
 
 
 file_identifier_system 
 count 
 
 
 
 
 GDC 
 1111

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
    
Finally, Julia uses the pagenation function again to get all the slide files, and merges her metadata file with this file information. This way she will be able to review what phenotypes each slide is associated with:

In [27]:
slides = NoadenoJustSlides.researchsubject.file.run()
slidesdf = slides.auto_paginator(to_df=True)

Getting results from database

Total execution time: 0
                        min 7.449 sec 7449 ms

Output()

In [28]:
slidemetadata = pd.merge(slidesdf, 
                         allmetadata, 
                         left_on=("subject_id","researchsubject_id"),
                         right_on=("subject_id", "researchsubject_id"),
                         suffixes=("_slide", "_all"))
slidemetadata

file_id  \
0     79dea52e-0f01-432f-80d2-605d6053052e   
1     7bf22346-d3ab-4ff8-8568-541cbec1470c   
2     3a3f1e4b-9d8c-47d2-91dd-f779f2a36a40   
3     7e640239-613a-49ec-aa97-e6af328efe93   
4     a14a9dd7-5c0a-49d7-bc15-4ed2a483fd06   
...                                    ...   
1106  9bf82894-b9bb-4ed3-a365-cee3e2a56480   
1107  7a6c0676-f25f-4fd9-a975-d2e4c01c058c   
1108  3c9c7394-a1a7-41e3-b3d7-4b502c6c5b6c   
1109  b97eb4e2-e6af-4f62-a203-4751c183b4df   
1110  a5d047ba-6816-4c12-a971-03bded22f34d   

                                        file_identifier  \
0     [{'system': 'GDC', 'value': '79dea52e-0f01-432...   
1     [{'system': 'GDC', 'value': '7bf22346-d3ab-4ff...   
2     [{'system': 'GDC', 'value': '3a3f1e4b-9d8c-47d...   
3     [{'system': 'GDC', 'value': '7e640239-613a-49e...   
4     [{'system': 'GDC', 'value': 'a14a9dd7-5c0a-49d...   
...                                                 ...   
1106  [{'system': 'GDC', 'value': '9bf82894-b9bb-4ed...   
1107  [{'system': 'GDC', 'value': '7a6c0676-f25f-4fd...   
1108  [{'system': 'GDC', 'value': '3c9c7394-a1a7-41e...   
1109  [{'system': 'GDC', 'value': 'b97eb4e2-e6af-4f6...   
1110  [{'system': 'GDC', 'value': 'a5d047ba-6816-4c1...   

                                                  label data_category  \
0     TCGA-N6-A4VF-01A-03-TSC.C6837FF0-A19E-4D16-A1B...   Biospecimen   
1     TCGA-N6-A4VF-11A-01-TSA.07939203-9432-431E-96D...   Biospecimen   
2     TCGA-N6-A4VF-01Z-00-DX1.D78EF5C0-E015-42DB-8D4...   Biospecimen   
3     TCGA-QN-A5NN-01Z-00-DX2.0FE8A3DA-ABAD-4517-9D4...   Biospecimen   
4     TCGA-QN-A5NN-01Z-00-DX4.AB57D943-2A7C-46E8-AD2...   Biospecimen   
...                                                 ...           ...   
1106  TCGA-C5-A1BK-01B-01-TS1.86c00487-ef71-4272-96c...   Biospecimen   
1107  TCGA-C5-A1BK-01Z-00-DX1.B01FAC89-30CC-4CDB-910...   Biospecimen   
1108  TCGA-PN-A8MA-01A-01-DX1.978164EB-6260-45BA-A87...   Biospecimen   
1109  TCGA-C5-A907-01A-01-TS1.E0D13713-6294-47D5-9D0...   Biospecimen   
1110  TCGA-C5-A907-01Z-00-DX1.7DEEFC23-B631-419E-B5E...   Biospecimen   

        data_type file_format file_associated_project  \
0     Slide Image         SVS              [TCGA-UCS]   
1     Slide Image         SVS              [TCGA-UCS]   
2     Slide Image         SVS              [TCGA-UCS]   
3     Slide Image         SVS              [TCGA-UCS]   
4     Slide Image         SVS              [TCGA-UCS]   
...           ...         ...                     ...   
1106  Slide Image         SVS             [TCGA-CESC]   
1107  Slide Image         SVS             [TCGA-CESC]   
1108  Slide Image         SVS             [TCGA-CESC]   
1109  Slide Image         SVS             [TCGA-CESC]   
1110  Slide Image         SVS             [TCGA-CESC]   

                                                drs_uri   byte_size  \
0     drs://dg.4DFC:79dea52e-0f01-432f-80d2-605d6053...    89647451   
1     drs://dg.4DFC:7bf22346-d3ab-4ff8-8568-541cbec1...    47409767   
2     drs://dg.4DFC:3a3f1e4b-9d8c-47d2-91dd-f779f2a3...  1465712675   
3     drs://dg.4DFC:7e640239-613a-49ec-aa97-e6af328e...  1477683125   
4     drs://dg.4DFC:a14a9dd7-5c0a-49d7-bc15-4ed2a483...  1999093775   
...                                                 ...         ...   
1106  drs://dg.4DFC:9bf82894-b9bb-4ed3-a365-cee3e2a5...   175306257   
1107  drs://dg.4DFC:7a6c0676-f25f-4fd9-a975-d2e4c01c...  1589829656   
1108  drs://dg.4DFC:3c9c7394-a1a7-41e3-b3d7-4b502c6c...    88338500   
1109  drs://dg.4DFC:b97eb4e2-e6af-4f62-a203-4751c183...   257797557   
1110  drs://dg.4DFC:a5d047ba-6816-4c12-a971-03bded22...   300025421   

                              checksum  ...  \
0     ffb1321391581951ad03a5bd18f7e0b4  ...   
1     aafe80885eaeaf41569e7b09cf950edd  ...   
2     b0feb735368ad896c369aabad27873b9  ...   
3     3936fa9a7ad9924d74abf2627f116694  ...   
4     b6b33e61eaba4c0bc787f27638986c8b  ...   
...                                ...  ...   
1106  e92d388fc448d48b43b5bc5

In [29]:
slidemetadata.count()

file_id                        1111
file_identifier                1111
label                          1111
data_category                  1111
data_type                      1111
file_format                    1111
file_associated_project        1111
drs_uri                        1111
byte_size                      1111
checksum                       1111
data_modality                  1111
imaging_modality                  0
dbgap_accession_number            0
imaging_series                    0
researchsubject_id             1111
subject_id                     1111
researchsubject_identifier     1111
member_of_research_project     1111
primary_diagnosis_condition    1111
primary_diagnosis_site         1111
subject_identifier             1111
species                        1111
sex                            1099
race                           1099
ethnicity                      1099
days_to_birth                     0
subject_associated_project     1111
vital_status                   1099
days_to_death                     0
cause_of_death                    0
dtype: int64

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Examples/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
    
Julia saves this dataframe to a csv as well, and now she has all the information she needs to begin work on her project. She can use the `drs_id` column information to directly download the images she is interested in using a DRS resolver, or she can input the DRS IDs at a cloud workspace such as [Terra](https://terra.bio/) or the [Cancer Genomics Cloud](https://www.cancergenomicscloud.org/) to view the images online. In either case, she has all the metadata she needs to get started, and can save this notebook of her work in case she'd like to come back and modify her search.

In [30]:
slidemetadata.to_csv("slidemetadata.csv")